## DT on House Prices dataset

In [8]:
import pandas as pd
import numpy as np
%matplotlib inline
import sklearn.model_selection as cv
import sklearn         
import matplotlib.pyplot as plt

from statsmodels.stats.proportion import proportion_confint


In [9]:
## Load dataset
data = pd.read_csv('../datasets/preprocessed/train.csv', sep=',')
data.head()

Id MSSubClass MSZoning   LotArea  LotShape LandContour LotConfig  \
0  0.000000          F       RL  0.249485       1.0         Lvl    Inside   
1  0.000685          A       RL  0.289612       1.0         Lvl        FR   
2  0.001371          F       RL  0.347186       0.0         Lvl    Inside   
3  0.002056          G       RL  0.287868       0.0         Lvl    Corner   
4  0.002742          F       RL  0.452214       0.0         Lvl        FR   

  Neighborhood Condition1 BldgType  ... Fence  MiscVal  SaleType  \
0      CollgCr       Norm     1Fam  ...   0.0      0.0        WD   
1      Veenker      Feedr     1Fam  ...   0.0      0.0        WD   
2      CollgCr       Norm     1Fam  ...   0.0      0.0        WD   
3      Crawfor       Norm     1Fam  ...   0.0      0.0        WD   
4      NoRidge       Norm     1Fam  ...   0.0      0.0        WD   

  SaleCondition SalePrice MasVnr  SecondFloor Baths Porch Pool  
0        Normal    Level3    1.0          1.0   0.6  True  0.0  
1        Normal    Level2    0.0          0.0   0.4  True  0.0  
2        Normal    Level3    1.0          1.0   0.6  True  0.0  
3       Abnorml    Level2    0.0          1.0   0.2  True  0.0  
4        Normal    Level3    1.0          1.0   0.6  True  0.0  

[5 rows x 48 columns]

In [10]:
## Separate data from labels
Y = data['SalePrice']
X = data.select_dtypes(include=['bool','object']) ## select categorical data FALTAN!!!
X = X.drop(['SalePrice'], axis=1) 

print(X.shape)
X.head()
#print(X.dtypes)

(1438, 25)


MSSubClass MSZoning LandContour LotConfig Neighborhood Condition1 BldgType  \
0          F       RL         Lvl    Inside      CollgCr       Norm     1Fam   
1          A       RL         Lvl        FR      Veenker      Feedr     1Fam   
2          F       RL         Lvl    Inside      CollgCr       Norm     1Fam   
3          G       RL         Lvl    Corner      Crawfor       Norm     1Fam   
4          F       RL         Lvl        FR      NoRidge       Norm     1Fam   

  HouseStyle RoofStyle RoofMatl  ... Functional  FireplaceQu GarageType  \
0     2Story     Gable  CompShg  ...        Typ  NoFireplace     Attchd   
1     1Story     Gable  CompShg  ...        Typ           TA     Attchd   
2     2Story     Gable  CompShg  ...        Typ           TA     Attchd   
3     2Story     Gable  CompShg  ...        Typ           Gd     Detchd   
4     2Story     Gable  CompShg  ...        Typ           TA     Attchd   

  GarageFinish GarageQual GarageCond PavedDrive SaleType SaleCondition Porch  
0          RFn         TA         TA          Y       WD        Normal  True  
1          RFn         TA         TA          Y       WD        Normal  True  
2          RFn         TA         TA          Y       WD        Normal  True  
3          Unf         TA         TA          Y       WD       Abnorml  True  
4          RFn         TA         TA          Y       WD        Normal  True  

[5 rows x 25 columns]

In [11]:
## Transform to numerical dataset
Xn=pd.get_dummies(X)
Xn.head()

Porch  MSSubClass_A  MSSubClass_B  MSSubClass_C  MSSubClass_D  \
0   True             0             0             0             0   
1   True             1             0             0             0   
2   True             0             0             0             0   
3   True             0             0             0             0   
4   True             0             0             0             0   

   MSSubClass_E  MSSubClass_F  MSSubClass_G  MSSubClass_H  MSSubClass_I  ...  \
0             0             1             0             0             0  ...   
1             0             0             0             0             0  ...   
2             0             1             0             0             0  ...   
3             0             0             1             0             0  ...   
4             0             1             0             0             0  ...   

   SaleType_ConLw  SaleType_New  SaleType_Oth  SaleType_WD  \
0               0             0             0            1   
1               0             0             0            1   
2               0             0             0            1   
3               0             0             0            1   
4               0             0             0            1   

   SaleCondition_Abnorml  SaleCondition_AdjLand  SaleCondition_Alloca  \
0                      0                      0                     0   
1                      0                      0                     0   
2                      0                      0                     0   
3                      1                      0                     0   
4                      0                      0                     0   

   SaleCondition_Family  SaleCondition_Normal  SaleCondition_Partial  
0                     0                     1                      0  
1                     0                     1                      0  
2                     0                     1                      0  
3                     0                     0                      0  
4                     0                     1                      0  

[5 rows x 172 columns]

In [12]:
## Split into training and test
from sklearn.utils import shuffle

Xn, Y = shuffle(Xn, Y)
(X_train, X_test,  y_train, y_test) = cv.train_test_split(Xn, Y, test_size=.3, random_state=10) #random_state=1

In [13]:
## Train and Print A Decision Tree

from sklearn import tree

clf = tree.DecisionTreeClassifier(criterion='entropy')
pred = clf.fit(X_train, y_train).predict(X_test)
print(sklearn.metrics.confusion_matrix(y_test, pred))
print()
print("Accuracy on test set:", sklearn.metrics.accuracy_score(y_test, pred))
print()
print(sklearn.metrics.classification_report(y_test, pred))
epsilon = sklearn.metrics.accuracy_score(y_test, pred)
print("Confidence interval: ",proportion_confint(count=epsilon*X_test.shape[0], nobs=X_test.shape[0], alpha=0.05, method='binom_test'))

# Print tree
fig = plt.gcf()
fig.set_size_inches(200, 100)

tree.plot_tree(clf, filled=True,rounded=True,feature_names=list(Xn.columns.values))
fig.savefig('tree.png')
plt.show()

[[ 15  20   0   0   0]
 [ 20 215  36   3   0]
 [  0  36  48  13   0]
 [  0   2   7   8   1]
 [  0   1   2   3   2]]

Accuracy on test set: 0.6666666666666666

              precision    recall  f1-score   support

      Level1       0.43      0.43      0.43        35
      Level2       0.78      0.78      0.78       274
      Level3       0.52      0.49      0.51        97
      Level4       0.30      0.44      0.36        18
      Level5       0.67      0.25      0.36         8

    accuracy                           0.67       432
   macro avg       0.54      0.48      0.49       432
weighted avg       0.67      0.67      0.67       432

Confidence interval:  (0.6204568375496147, 0.709671829828461)


In [14]:
# Cross-validation of the first model 
scores = sklearn.model_selection.cross_val_score(clf, Xn, Y, cv=10)
print("Accuracy on 10 fold cross-validation:", scores)
print(np.mean(scores))

Accuracy on 10 fold cross-validation: [0.72222222 0.67361111 0.66666667 0.72222222 0.72222222 0.68055556
 0.66666667 0.65277778 0.68531469 0.65734266]
0.6849601787101787


In [15]:
## Train and Print A Decision Tree ()

clf=tree.DecisionTreeClassifier(criterion='entropy', min_samples_split=2,min_impurity_decrease=0.02)
clf = clf.fit(X_train, y_train)
pred = clf.predict(X_test)

# Obtain accuracy score of learned classifier on test data
print(clf.score(X_test, y_test))
print(sklearn.metrics.confusion_matrix(y_test, pred))
print()
print("Accuracy:", sklearn.metrics.accuracy_score(y_test, pred))
print()
print(sklearn.metrics.classification_report(y_test, pred))
epsilon = sklearn.metrics.accuracy_score(y_test, pred)
print("Interval of confidence:", proportion_confint(count=epsilon*X_test.shape[0], nobs=X_test.shape[0], alpha=0.05, method='binom_test'))

# Print tree
fig = plt.gcf()
fig.set_size_inches(800, 80)

tree.plot_tree(clf, filled=True,rounded=True)
fig.savefig('tree.png')
plt.show()

0.6319444444444444
[[ 15  20   0   0   0]
 [ 25 246   0   3   0]
 [  0  79   3  15   0]
 [  0   6   3   9   0]
 [  0   1   1   6   0]]

Accuracy: 0.6319444444444444

              precision    recall  f1-score   support

      Level1       0.38      0.43      0.40        35
      Level2       0.70      0.90      0.79       274
      Level3       0.43      0.03      0.06        97
      Level4       0.27      0.50      0.35        18
      Level5       0.00      0.00      0.00         8

    accuracy                           0.63       432
   macro avg       0.36      0.37      0.32       432
weighted avg       0.58      0.63      0.56       432



C:\Users\Alex\Anaconda3\lib\site-packages\sklearn\metrics\_classification.py:1268: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Interval of confidence: (0.5845562588278561, 0.6772236105853114)


In [16]:
# Cross-validation of the previous model 
scores = sklearn.model_selection.cross_val_score(clf, Xn, Y, cv=10)
print("Accuracy on 10 fold cross-validation:", scores)
print(np.mean(scores))

Accuracy on 10 fold cross-validation: [0.68055556 0.67361111 0.68055556 0.70138889 0.625      0.65972222
 0.68055556 0.64583333 0.62937063 0.69230769]
0.6668900543900544


In [25]:
# Search of the best params
from sklearn.model_selection import GridSearchCV

params = {'min_impurity_decrease': list(np.linspace(0,0.5,21)),'min_samples_split':list(range(2,20,11))}
clf = GridSearchCV(tree.DecisionTreeClassifier(criterion='entropy'), param_grid=params,cv=10,n_jobs=-1)  # If cv is integer, by default is Stratifyed 
clf.fit(X_train, y_train)
print("Best Params=",clf.best_params_, "Accuracy=", clf.best_score_)

Best Params= {'min_impurity_decrease': 0.0, 'min_samples_split': 2} Accuracy= 0.691009900990099


In [ ]:
## Train and Print A Decision Tree (with best params)

clf = tree.DecisionTreeClassifier(criterion='entropy', min_samples_split=clf.best_params_['min_samples_split'],min_impurity_decrease=clf.best_params_['min_impurity_decrease'])
clf = clf.fit(X_train, y_train)
pred = clf.predict(X_test)

# Obtain accuracy score of learned classifier on test data
print(clf.score(X_test, y_test))
print(sklearn.metrics.confusion_matrix(y_test, pred))
print()
print("Accuracy:", sklearn.metrics.accuracy_score(y_test, pred))
print()
print(sklearn.metrics.classification_report(y_test, pred))
epsilon = sklearn.metrics.accuracy_score(y_test, pred)
print("Interval of confidence:", proportion_confint(count=epsilon*X_test.shape[0], nobs=X_test.shape[0], alpha=0.05, method='binom_test'))

# Print tree
fig = plt.gcf()
fig.set_size_inches(800, 80)

tree.plot_tree(clf, filled=True,rounded=True)
fig.savefig('treeBestParams.png')
plt.show()

0.6550925925925926
[[ 17  18   0   0   0]
 [ 22 213  36   3   0]
 [  0  37  45  15   0]
 [  0   2   9   6   1]
 [  0   2   2   2   2]]

Accuracy: 0.6550925925925926

              precision    recall  f1-score   support

      Level1       0.44      0.49      0.46        35
      Level2       0.78      0.78      0.78       274
      Level3       0.49      0.46      0.48        97
      Level4       0.23      0.33      0.27        18
      Level5       0.67      0.25      0.36         8

    accuracy                           0.66       432
   macro avg       0.52      0.46      0.47       432
weighted avg       0.66      0.66      0.66       432

Interval of confidence: (0.6088707467170716, 0.6992235784453159)


In [23]:
# Cross-validation of the model with best params
scores = sklearn.model_selection.cross_val_score(clf, Xn, Y, cv=10)
print("Accuracy on 10 fold cross-validation:", scores)
print(np.mean(scores))

Accuracy on 10 fold cross-validation: [0.74305556 0.67361111 0.68055556 0.6875     0.70138889 0.67361111
 0.72916667 0.6875     0.67832168 0.6993007 ]
0.6954011266511266
